# Item-based Models

In this file we are going to proceed with the building in the models. Machine learning models to build recommender systems. The models that are going to be built are Collaborative filtering using Item-based rating prediction (ItemKNN) and Item-based classification (ItemKNN).

Collaborative filtering is a technique used in recommendation systems to predict or classify items based on the preferences or behavior of similar users or items. Item-based Collaborative Filtering (CF) focuses on the similarity between items rather than users. There are two main approaches within item-based CF: rating prediction and classification.

In [1]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all" # to make jupyter print all outputs, not just the last one
from IPython.core.display import HTML # to pretty print pandas df and be able to copy them over (e.g. to ppt slides)

In [2]:
# We import the necessary libraries
import pandas as pd
import numpy as np
import os

In [3]:
# We print the directory where the file is located
print(os.getcwd())

c:\Users\Jaume\Documents\MDDB\SDM\SDfM---Jaume-and-Stijn 2\SDfM---Jaume-and-Stijn


In [4]:
# We set the directory to the cleaned folder
os.listdir(os.path.join('.', 'cleaned'))

['final_sample30_parquet',
 'final_sample50_parquet',
 'final_sample5_parquet',
 'final_strat_sample_parquet',
 'movielens_parquet',
 'movielens_parquet_small',
 'netflix_parquet',
 'sample_tenth_netflix',
 'strat_sample_movielens',
 'strat_sample_netflix']

In [5]:
# We read the final_sample file and store it in a dataframe
df = pd.read_parquet('cleaned/strat_sample_netflix')

In [6]:
# We print shape of the dataframe
df.shape

(80, 7)

In [7]:
# We print the first 5 rows of the dataframe
df.head()

movieId                                        review_data  \
1112     1113  [{'date': 2004-05-03, 'rating': 2.0, 'userId':...   
1412     1413  [{'date': 2005-07-11, 'rating': 4.0, 'userId':...   
1311     1312  [{'date': 2005-08-27, 'rating': 4.0, 'userId':...   
1792     1793  [{'date': 2003-07-29, 'rating': 4.0, 'userId':...   
1510     1511  [{'date': 2005-08-17, 'rating': 4.0, 'userId':...   

                               genres  year  \
1112      [Animation, Comedy, Sci-Fi]  1998   
1412  [Documentary, Biography, Sport]  1998   
1311           [Action, Crime, Drama]  1990   
1792                             None  1992   
1510                  [Drama, Sci-Fi]  2000   

                                            title review_stratum  num_reviews  
1112                                Lost Universe             Q2          371  
1412         The Life and Times of Hank Greenberg             Q2          883  
1311                                 The Prisoner             Q2          432  
1792  Sailor Moon: Vol. 10: The Trouble With Rini             Q2          436  
1510                                 On the Beach             Q2          476

In [8]:
# We print the columns of the dataframe
df.columns

Index(['movieId', 'review_data', 'genres', 'year', 'title', 'review_stratum',
       'num_reviews'],
      dtype='object')

In [9]:
df = df[df['review_data'].apply(lambda x: len(x) if x is not None else 0) > 100]

In [10]:
# Step 1: Explode the review_data column
exploded_df = df.explode('review_data').reset_index(drop=True)


In [11]:
exploded_df.head()

exploded_df.shape

# We get the first row of exploded_df
exploded_df.iloc[0]

movieId                                        review_data  \
0     1113  {'date': 2004-05-03, 'rating': 2.0, 'userId': ...   
1     1113  {'date': 2003-09-15, 'rating': 4.0, 'userId': ...   
2     1113  {'date': 2004-01-08, 'rating': 1.0, 'userId': ...   
3     1113  {'date': 2003-12-02, 'rating': 4.0, 'userId': ...   
4     1113  {'date': 2004-05-03, 'rating': 5.0, 'userId': ...   

                        genres  year          title review_stratum  \
0  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   
1  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   
2  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   
3  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   
4  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   

   num_reviews  
0          371  
1          371  
2          371  
3          371  
4          371

(452604, 7)

movieId                                                        1113
review_data       {'date': 2004-05-03, 'rating': 2.0, 'userId': ...
genres                                  [Animation, Comedy, Sci-Fi]
year                                                           1998
title                                                 Lost Universe
review_stratum                                                   Q2
num_reviews                                                     371
Name: 0, dtype: object

In [12]:
# Step 2: Convert the exploded dictionary column into separate columns
expanded_review_data = pd.json_normalize(exploded_df['review_data'])


In [13]:
expanded_review_data.head()

date  rating   userId
0  2004-05-03     2.0  1945809
1  2003-09-15     4.0    41412
2  2004-01-08     1.0   305151
3  2003-12-02     4.0   497196
4  2004-05-03     5.0    76196

In [14]:
# Step 3: Concatenate the expanded data with the original DataFrame
df = pd.concat([exploded_df.drop('review_data', axis=1), expanded_review_data], axis=1)

# Verify the shape of the final DataFrame
print("Final DataFrame shape:", df.shape)


Final DataFrame shape: (452604, 9)


In [15]:
df.head()

movieId                       genres  year          title review_stratum  \
0     1113  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   
1     1113  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   
2     1113  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   
3     1113  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   
4     1113  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   

   num_reviews        date  rating   userId  
0          371  2004-05-03     2.0  1945809  
1          371  2003-09-15     4.0    41412  
2          371  2004-01-08     1.0   305151  
3          371  2003-12-02     4.0   497196  
4          371  2004-05-03     5.0    76196

In [16]:
# We print the number of unique users and movies
print(df['userId'].nunique())
print(df['movieId'].nunique())


202747
78


In [17]:
# Check if there are userIDs that haven't rated movies at all
print(df['userId'].value_counts().sort_values(ascending=False))

# Check if there are movieIDs that haven't been rated at all
print(df['movieId'].value_counts().sort_values(ascending=False))

userId
305344     78
387418     78
2439493    75
1664010    72
2118461    65
           ..
1073132     1
1600018     1
2221375     1
2548691     1
1029317     1
Name: count, Length: 202747, dtype: int64
movieId
482     56504
406     48617
1659    42046
1046    40744
1174    35537
        ...  
236       125
1440      115
945       113
43        105
1829      102
Name: count, Length: 78, dtype: int64


In [18]:
# Get the rating for movieID 4966
df[df['movieId'] == 4966]

Empty DataFrame
Columns: [movieId, genres, year, title, review_stratum, num_reviews, date, rating, userId]
Index: []

In [19]:
# Check if there are NaN values in the rating column
df['rating'].isna().sum()

0

In [20]:
# Step 1: Group the DataFrame by 'userId' and count the number of ratings per user
user_rating_counts = df.groupby('userId').size()

# Step 2: Filter out users who have rated less than 3 movies
active_users = user_rating_counts[user_rating_counts >= 3].index.tolist()

# Step 3: Select rows from the original DataFrame for active users
df = df[df['userId'].isin(active_users)]

# Display the filtered DataFrame
df.head()


movieId                       genres  year          title review_stratum  \
0     1113  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   
1     1113  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   
2     1113  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   
3     1113  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   
4     1113  [Animation, Comedy, Sci-Fi]  1998  Lost Universe             Q2   

   num_reviews        date  rating   userId  
0          371  2004-05-03     2.0  1945809  
1          371  2003-09-15     4.0    41412  
2          371  2004-01-08     1.0   305151  
3          371  2003-12-02     4.0   497196  
4          371  2004-05-03     5.0    76196

In [21]:
# We take a sample of 10% of the data
df = df.sample(frac=0.2, random_state=42)

In [22]:
# Verify the shape of the final DataFrame
print("Final DataFrame shape:", df.shape)

Final DataFrame shape: (52317, 9)


# Item-based Rating Prediction (ItemKNN)

### Step 1: User-Item matrix construction
The first thing we have to do is build the user-item matrix:

- Choose a similarity metric to calculate the similarity between items. Common metrics include cosine similarity, Pearson correlation coefficient, and Jaccard similarity.
- Calculate the similarity between each pair of items based on the ratings provided by users. This will result in an item-item similarity matrix.

#### Collaborative Filtering with Cosine Similarity

This code snippet demonstrates how to perform item-based collaborative filtering using cosine similarity. Collaborative filtering is a technique commonly used in recommendation systems to predict a user's preferences for items based on the preferences of similar users/items.

##### Libraries Used
- **pandas**: A powerful data manipulation library in Python.
- **numpy**: A library for numerical computing in Python.
- **sklearn.metrics.pairwise.cosine_similarity**: A function from scikit-learn used to compute the cosine similarity between vectors.

In [23]:
import pandas as pd
import numpy as np

# Convert userId column to integer type if needed
if df['userId'].dtype != int:
    df['userId'] = df['userId'].astype(int)

# Get all unique user IDs and movie IDs
all_user_ids = np.unique(df['userId'])
all_movie_ids = np.unique(df['movieId'])

# Determine the number of unique users and movies
num_users = len(all_user_ids)
num_movies = len(all_movie_ids)

# Create a dictionary to store ratings for each user
user_ratings = {}

# Iterate through the DataFrame and populate the user_ratings dictionary
for _, row in df.iterrows():
    user_id = row['userId']
    movie_id = row['movieId']
    rating = row['rating']
    
    # Initialize the user's ratings list if not already present
    if user_id not in user_ratings:
        user_ratings[user_id] = np.zeros(num_movies)
    
    # Assign the rating to the corresponding movie index
    user_ratings[user_id][np.where(all_movie_ids == movie_id)[0][0]] = rating

# Create user-item matrix from the dictionary
item_user_matrix = pd.DataFrame(user_ratings.values(), index=user_ratings.keys(), columns=all_movie_ids)

# Convert user-item matrix to NumPy array for faster computation
item_user_array = item_user_matrix.to_numpy()


In [24]:
item_user_matrix.head()

43    44    58    155   166   168   213   226   236   239   ...  \
1509395   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
1188945   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
2568178   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
1438764   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
362622    0.0   0.0   0.0   0.0   0.0   0.0   3.0   0.0   0.0   0.0  ...   

         1768  1793  1821  1829  1830  1839  1851  1854  1855  1903  
1509395   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
1188945   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
2568178   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
1438764   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
362622    0.0   0.0   0.0   0.0   0.0   0.0   4.0   0.0   0.0   0.0  

[5 rows x 78 columns]

In [25]:
item_user_array

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

### Train-test split

The train-val-test split is a technique used in machine learning to evaluate the performance of a model. It involves dividing the dataset into three subsets: the training set, the validation set, and the test set.

The training set is used to train the model and optimize its parameters.
The validation set is used to fine-tune the model and select the best hyperparameters.
The test set is used to evaluate the final performance of the model on unseen data.
By using a train-val-test split, we can assess the model's performance on unseen data and ensure that it generalizes well to new examples. It helps prevent overfitting and provides a more reliable estimate of the model's performance in real-world scenarios.

In [26]:
from sklearn.model_selection import train_test_split
# Split the data into training and test sets
train_val, test = train_test_split(item_user_array, test_size=0.2, random_state=42)

# Split the training set into training and validation sets
train, val = train_test_split(train_val, test_size=0.2, random_state=42)

# Print the shapes of the datasets
print("Training set shape:", train.shape)
print("Validation set shape:", val.shape)
print("Test set shape:", test.shape)

# We are also going to do the split for the matrix df
# Split the user-item matrix into training and test sets
train_val_matrix, test_matrix = train_test_split(item_user_matrix, test_size=0.2, random_state=42)

# Split the training set matrix into training and validation sets
train_matrix, val_matrix = train_test_split(train_val_matrix, test_size=0.2, random_state=42)

# We print a ' ' to give some space inbetween lines
print(' ')

# Print the shapes of the matrix datasets
print("Training set matrix shape:", train_matrix.shape)
print("Validation set matrix shape:", val_matrix.shape)
print("Test set matrix shape:", test_matrix.shape)


Training set shape: (21923, 78)
Validation set shape: (5481, 78)
Test set shape: (6852, 78)
 
Training set matrix shape: (21923, 78)
Validation set matrix shape: (5481, 78)
Test set matrix shape: (6852, 78)


In [27]:
train_matrix

43    44    58    155   166   168   213   226   236   239   ...  \
751126    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
1772875   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
1832869   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
342396    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
1506336   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
...       ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
1304853   0.0   0.0   3.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
185495    0.0   0.0   0.0   0.0   3.0   0.0   0.0   0.0   0.0   0.0  ...   
41317     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
796472    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
532583    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   

         1768  1793  1821  1829  1830  1839  1851  1854  1855  1903  
751126    0.0   0.0   0.0   0.0   0.0   0.0   0.0   3.0   0.0   0.0  
1772875   0.0   0.0   0.0   0.0   0.0   3.0   0.0   0.0   0.0   0.0  
1832869   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
342396    0.0   0.0   0.0   0.0   0.0   0.0   0.0   3.0   0.0   0.0  
1506336   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
...       ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
1304853   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
185495    0.0   0.0   0.0   0.0   0.0   0.0   0.0   4.0   0.0   0.0  
41317     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
796472    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
532583    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  

[21923 rows x 78 columns]

In [28]:
train

array([[0., 0., 0., ..., 3., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [29]:
# Calculate cosine similarity between items using NumPy functions
def cosine_similarity(a, b):
    dot_product = np.dot(a, b)
    norm_a = np.linalg.norm(a)
    norm_b = np.linalg.norm(b)
    similarity = dot_product / (norm_a * norm_b)
    return similarity

# Calculate item-item similarity matrix for train data
#item_similarity_matrix_train = np.zeros((train.shape[1], train.shape[1]))

#for i in range(train.shape[1]):
 #   for j in range(i, train.shape[1]):
  #      item_similarity_matrix_train[i, j] = cosine_similarity(train[:, i], train[:, j])
   #     item_similarity_matrix_train[j, i] = item_similarity_matrix_train[i, j]

# Adjusting the mapping to start indexing from 0
user_id_to_index = {user_id: i for i, user_id in enumerate(item_user_matrix.index)}
index_to_user_id = {i: user_id for i, user_id in enumerate(item_user_matrix.index)}

# Create a mapping from movie IDs to indices
movie_id_to_index = {movie_id: i for i, movie_id in enumerate(item_user_matrix.columns)}
index_to_movie_id = {i: movie_id for i, movie_id in enumerate(item_user_matrix.columns)}




In [30]:
# Step 2: Calculate the item-item similarity matrix for the train set
def calculate_item_similarity_matrix(data):
    item_similarity_matrix = np.zeros((data.shape[1], data.shape[1]))

    for i in range(data.shape[1]):
        for j in range(i, data.shape[1]):
            item_similarity_matrix[i, j] = cosine_similarity(data[:, i], data[:, j])
            item_similarity_matrix[j, i] = item_similarity_matrix[i, j]

    return item_similarity_matrix

item_similarity_matrix_train = calculate_item_similarity_matrix(train)

In [31]:
item_similarity_matrix_train

array([[1.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 1.        , 0.02214396, ..., 0.04477643, 0.00213857,
        0.        ],
       [0.        , 0.02214396, 1.        , ..., 0.03089202, 0.00978001,
        0.        ],
       ...,
       [0.        , 0.04477643, 0.03089202, ..., 1.        , 0.00825127,
        0.        ],
       [0.        , 0.00213857, 0.00978001, ..., 0.00825127, 1.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        1.        ]])

In [32]:
movie_id_to_index

{43: 0,
 44: 1,
 58: 2,
 155: 3,
 166: 4,
 168: 5,
 213: 6,
 226: 7,
 236: 8,
 239: 9,
 268: 10,
 309: 11,
 327: 12,
 406: 13,
 448: 14,
 451: 15,
 458: 16,
 477: 17,
 482: 18,
 492: 19,
 507: 20,
 524: 21,
 528: 22,
 529: 23,
 531: 24,
 550: 25,
 641: 26,
 681: 27,
 695: 28,
 726: 29,
 750: 30,
 766: 31,
 818: 32,
 836: 33,
 843: 34,
 849: 35,
 852: 36,
 897: 37,
 945: 38,
 1005: 39,
 1040: 40,
 1046: 41,
 1061: 42,
 1098: 43,
 1099: 44,
 1113: 45,
 1117: 46,
 1174: 47,
 1248: 48,
 1252: 49,
 1303: 50,
 1312: 51,
 1361: 52,
 1389: 53,
 1413: 54,
 1414: 55,
 1420: 56,
 1440: 57,
 1511: 58,
 1526: 59,
 1552: 60,
 1553: 61,
 1560: 62,
 1573: 63,
 1579: 64,
 1611: 65,
 1659: 66,
 1731: 67,
 1768: 68,
 1793: 69,
 1821: 70,
 1829: 71,
 1830: 72,
 1839: 73,
 1851: 74,
 1854: 75,
 1855: 76,
 1903: 77}

In [33]:
print(index_to_user_id)

{0: 1509395, 1: 1188945, 2: 2568178, 3: 1438764, 4: 362622, 5: 2002250, 6: 1593815, 7: 366815, 8: 1555461, 9: 1641738, 10: 189199, 11: 1538119, 12: 1266864, 13: 912340, 14: 740947, 15: 335178, 16: 1073396, 17: 570532, 18: 1316866, 19: 483107, 20: 2386069, 21: 1192767, 22: 1525786, 23: 2296114, 24: 1969536, 25: 2294239, 26: 1073354, 27: 2237757, 28: 1085049, 29: 1106186, 30: 2256731, 31: 98301, 32: 253785, 33: 495271, 34: 1519860, 35: 2449356, 36: 1123449, 37: 872102, 38: 1981741, 39: 1501752, 40: 517066, 41: 1607009, 42: 247747, 43: 2302235, 44: 514870, 45: 1891888, 46: 1387099, 47: 1430656, 48: 1754009, 49: 1656801, 50: 634388, 51: 2310880, 52: 65076, 53: 1182493, 54: 184544, 55: 540803, 56: 680273, 57: 1505434, 58: 679869, 59: 1363778, 60: 846426, 61: 2474943, 62: 2337937, 63: 2017649, 64: 2040859, 65: 1658101, 66: 1378330, 67: 2347167, 68: 1685912, 69: 1217870, 70: 412883, 71: 1921954, 72: 825576, 73: 1624864, 74: 1819462, 75: 1192958, 76: 767590, 77: 410007, 78: 1595055, 79: 165512

In [34]:
print(user_id_to_index)

{1509395: 0, 1188945: 1, 2568178: 2, 1438764: 3, 362622: 4, 2002250: 5, 1593815: 6, 366815: 7, 1555461: 8, 1641738: 9, 189199: 10, 1538119: 11, 1266864: 12, 912340: 13, 740947: 14, 335178: 15, 1073396: 16, 570532: 17, 1316866: 18, 483107: 19, 2386069: 20, 1192767: 21, 1525786: 22, 2296114: 23, 1969536: 24, 2294239: 25, 1073354: 26, 2237757: 27, 1085049: 28, 1106186: 29, 2256731: 30, 98301: 31, 253785: 32, 495271: 33, 1519860: 34, 2449356: 35, 1123449: 36, 872102: 37, 1981741: 38, 1501752: 39, 517066: 40, 1607009: 41, 247747: 42, 2302235: 43, 514870: 44, 1891888: 45, 1387099: 46, 1430656: 47, 1754009: 48, 1656801: 49, 634388: 50, 2310880: 51, 65076: 52, 1182493: 53, 184544: 54, 540803: 55, 680273: 56, 1505434: 57, 679869: 58, 1363778: 59, 846426: 60, 2474943: 61, 2337937: 62, 2017649: 63, 2040859: 64, 1658101: 65, 1378330: 66, 2347167: 67, 1685912: 68, 1217870: 69, 412883: 70, 1921954: 71, 825576: 72, 1624864: 73, 1819462: 74, 1192958: 75, 767590: 76, 410007: 77, 1595055: 78, 1655125: 7

In [35]:
item_user_array.shape

(34256, 78)

In [36]:
item_user_matrix.shape

(34256, 78)

In [37]:
# We print the item_similarity_matrix
item_similarity_matrix_train

array([[1.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 1.        , 0.02214396, ..., 0.04477643, 0.00213857,
        0.        ],
       [0.        , 0.02214396, 1.        , ..., 0.03089202, 0.00978001,
        0.        ],
       ...,
       [0.        , 0.04477643, 0.03089202, ..., 1.        , 0.00825127,
        0.        ],
       [0.        , 0.00213857, 0.00978001, ..., 0.00825127, 1.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        1.        ]])

In [38]:
item_similarity_matrix_train.shape

(78, 78)

### Step 2: Neighborhood Selection
- Determine the neighborhood size, i.e., the number of most similar items to consider when predicting ratings for a target item.
- Select the most similar items for each item in your dataset based on their calculated similarities. This forms the neighborhood for each item.

#### Item-Based Neighborhoods and Ratings Aggregation

This code following snippet enhances the previous item-based collaborative filtering approach by considering ratings aggregation within the item neighborhoods.

##### Steps:

1. **Defining Neighborhood Size**:
   - The variable `neighborhood_size` determines the number of most similar items to consider in the neighborhood.

2. **Initializing Data Structure**:
   - An empty dictionary `item_neighborhoods` is initialized to store the neighborhoods for each item.

3. **Iterating Over Items**:
   - For each movie in the dataset:
     - All ratings for the current movie are extracted from the DataFrame (`df`).
     - Ratings aggregation is performed. In this example, the average rating for the movie is computed, but other aggregation methods can be used.
     - The similarity scores for the current movie are retrieved from the precomputed `item_similarity_matrix`.
     - Similarity scores are sorted in descending order, and the indices of the most similar items (excluding itself) are obtained.
     - These indices are converted back to movie IDs, forming the neighborhood for the current item.
     - The neighborhood for the current item is stored in the `item_neighborhoods` dictionary.

4. **Output**:
   - `item_neighborhoods`: A dictionary where keys are movie IDs, and values are lists of movie IDs representing the neighborhood of each item. Each movie's neighborhood includes movies with similar ratings and content.

##### Note:
- This approach considers both similarity in ratings and content (as captured by cosine similarity) when building item neighborhoods.
- Aggregating ratings within item neighborhoods helps in providing more personalized recommendations.
- The choice of rating aggregation method (e.g., mean, median) can impact the quality of recommendations and may need to be adjusted based on the characteristics of the dataset and user preferences.


In [39]:
import numpy as np

def neighborhood_selection(item_user_array, index_to_movie_id, item_similarity_matrix, neighborhood_size=5):
    # Initialize an empty dictionary to store item neighborhoods
    item_neighborhoods = {}

    # Iterate over each item (movie) index in the dataset
    for movie_index in range(item_user_array.shape[1]):
        # Convert the item index to movie ID
        movie_id = index_to_movie_id[movie_index]

        # Extract all ratings for the current movie
        movie_ratings = item_user_array[:, movie_index]

        # Aggregate ratings (e.g., compute the mean rating)
        movie_avg_rating = np.mean(movie_ratings)

        # Retrieve similarity scores for the current movie
        similarity_scores = item_similarity_matrix[movie_index]

        # Sort similarity scores in descending order and get indices of most similar items
        most_similar_indices = np.argsort(similarity_scores)[::-1][1:neighborhood_size+1]

        # Convert indices back to movie IDs to form the neighborhood
        neighborhood = [index_to_movie_id[idx] for idx in most_similar_indices]

        # Store the neighborhood for the current item in the item_neighborhoods dictionary
        item_neighborhoods[movie_id] = neighborhood

    return item_neighborhoods

# Example usage:
item_neighborhoods_train = neighborhood_selection(item_user_array, index_to_movie_id, item_similarity_matrix_train)
print(item_neighborhoods_train)


{43: [1113, 852, 1573, 309, 1174], 44: [1659, 482, 524, 550, 1854], 58: [550, 1659, 818, 1174, 528], 155: [268, 529, 168, 58, 1046], 166: [550, 1174, 1046, 1659, 482], 168: [681, 155, 58, 1659, 529], 213: [1821, 482, 836, 1839, 226], 226: [1252, 1005, 1611, 1117, 213], 236: [1440, 1303, 1117, 695, 1099], 239: [1389, 1511, 236, 1440, 1303], 268: [155, 818, 507, 58, 550], 309: [836, 1511, 1793, 492, 1855], 327: [1855, 1731, 1413, 836, 1839], 406: [1174, 1046, 550, 1659, 528], 448: [1579, 1526, 492, 58, 406], 451: [681, 528, 155, 1793, 268], 458: [1793, 1414, 1252, 531, 1046], 477: [1731, 818, 1659, 406, 155], 482: [843, 1046, 897, 550, 1659], 492: [849, 1312, 524, 1851, 843], 507: [268, 818, 1579, 166, 641], 524: [44, 843, 482, 492, 818], 528: [406, 58, 1174, 1659, 482], 529: [155, 168, 1005, 1389, 1579], 531: [1414, 550, 897, 458, 1046], 550: [1659, 58, 1174, 1046, 406], 641: [849, 507, 58, 1839, 818], 681: [168, 1174, 1659, 550, 406], 695: [236, 1440, 1117, 1303, 1413], 726: [1117, 124

### Step 4: Rating Prediction

- For each target item and user pair where the user hasn't rated the target item:
Identify the neighborhood of similar items to the target item.
- Predict the rating for the target item using a weighted average of the ratings of the items in its neighborhood, where the weights are the similarities between the items and the target item.
- Adjust the prediction based on the user's average rating or other normalization techniques, if necessary.

In [40]:
# Train your model and create the item_neighborhoods dictionary using the training data (steps 1-3)

# Initialize an empty DataFrame to store predicted ratings
predicted_ratings_train = pd.DataFrame(index=train_matrix.index, columns=train_matrix.columns)

# Iterate over each user-item pair in the training set
for user_id, user_ratings in train_matrix.iterrows():
    for movie_id, rating in user_ratings.items():
        
        # Skip if the rating is non-zero (indicating a rating given by the user)
        if rating != 0:
            continue
        
        # Check if the movie has a neighborhood defined
        if movie_id in item_neighborhoods_train:
            neighborhood = item_neighborhoods_train[movie_id]
            
            # Filter out movies from the neighborhood that the user has rated in the training set
            filtered_neighborhood = [neighbor_movie_id for neighbor_movie_id in neighborhood if neighbor_movie_id in user_ratings.index and user_ratings.loc[neighbor_movie_id] != 0]
            
            # Check if there are valid indices in the filtered neighborhood
            if len(filtered_neighborhood) > 0:
                # Calculate the predicted rating for the target movie based on the neighborhood
                neighbor_ratings = [user_ratings.loc[neighbor_movie_id] for neighbor_movie_id in filtered_neighborhood]
                
                # Calculate the mean rating using only the movies in the neighborhood that have been rated by the user
                predicted_rating = np.mean(neighbor_ratings)
            else:
                # If the filtered neighborhood is empty, assign the mean rating of all movies rated by the user
                predicted_rating = user_ratings[user_ratings != 0].mean()
            
            # Assign the predicted rating to the corresponding cell in the DataFrame
            predicted_ratings_train.at[user_id, movie_id] = predicted_rating

# Fill NaN values with mean ratings across all users
predicted_ratings_train.fillna(predicted_ratings_train.mean().mean(), inplace=True)

# Display the head of the predicted_ratings DataFrame
predicted_ratings_train.head()


C:\Users\Jaume\AppData\Local\Temp\ipykernel_6308\1268806476.py:36: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  predicted_ratings_train.fillna(predicted_ratings_train.mean().mean(), inplace=True)


43    44    58    155   166   168   213   226   236   239   ...  \
751126   2.00   3.0   2.0   2.5   2.0  2.50   2.5  2.50  2.50  2.50  ...   
1772875  3.75   5.0   4.0   4.0   4.5  3.75   3.0  3.75  3.75  3.75  ...   
1832869  4.00   4.0   4.0   4.0   4.0  4.00   4.0  4.00  4.00  4.00  ...   
342396   3.00   3.0   3.0   3.0   3.0  3.00   3.0  3.00  3.00  3.00  ...   
1506336  3.50   3.5   3.5   4.0   4.0  3.50   3.5  3.50  3.50  3.50  ...   

         1768  1793  1821  1829  1830      1839  1851      1854  1855  1903  
751126    2.5  2.50  2.50  2.50   2.0  2.500000  2.50  3.530354  2.50   2.5  
1772875   3.0  3.75  3.75  3.75   3.0  3.530354  3.75  4.500000  3.75   4.0  
1832869   4.0  4.00  4.00  4.00   4.0  4.000000  4.00  4.000000  4.00   4.0  
342396    3.0  3.00  3.00  3.00   3.0  3.000000  3.00  3.530354  3.00   3.0  
1506336   3.5  3.50  3.50  3.00   3.0  3.500000  3.50  4.000000  3.50   4.0  

[5 rows x 78 columns]

In [41]:
# We count the NaN values in the predicted_ratings_train dataframe
predicted_ratings_train.isnull().sum().sum()

0

In [42]:
def get_top_recommendations(user_id, predicted_ratings, df):
    """
    Get top movie recommendations for a given user using predicted ratings.

    Parameters:
        user_id (int): ID of the user for whom recommendations are to be generated.
        predicted_ratings (pd.DataFrame): DataFrame containing predicted ratings for users and movies.
        df (pd.DataFrame): DataFrame containing movie ratings.

    Returns:
        list: Top movie titles recommended for the user.
    """
    # Ensure that predicted_ratings is a DataFrame
    if not isinstance(predicted_ratings, pd.DataFrame):
        raise ValueError("predicted_ratings must be a pandas DataFrame")

    # Check if the user ID exists in the predicted ratings DataFrame's index
    if user_id not in predicted_ratings.index:
        # If the user ID doesn't exist, return an empty list
        return ["The user doesn't exist"]

    # Get the predicted ratings for the user
    user_predicted_ratings = predicted_ratings.loc[user_id]
    
    # Filter out the movies that the user has already seen
    seen_movies = set(df[df['userId'] == user_id]['movieId'])
    unseen_movies = [movie_id for movie_id in user_predicted_ratings.index if movie_id not in seen_movies]
    
    # Check if there are unseen movies with predicted ratings
    if not unseen_movies:
        # If all movies have been seen, return an empty list
        return []
    
    # Sort the unseen movies by predicted rating in descending order
    sorted_unseen_movies = user_predicted_ratings[unseen_movies].sort_values(ascending=False)
    
    # Get the top 5 movie titles
    top_movie_ids = sorted_unseen_movies.head(5).index.tolist()
    
    # Get the unique movie titles corresponding to the top movie IDs
    top_movie_titles = set(df[df['movieId'].isin(top_movie_ids)]['title'])
    
    return list(top_movie_titles)[:5]  # Return only the first 5 unique movie titles


In [43]:
top_recommendations = []

# Iterate over each row (user) in the train_matrix
for user_id in train_matrix.index:
    # Get the actual user ID corresponding to the user index
    recommendations = get_top_recommendations(user_id, predicted_ratings_train, df)
    top_recommendations.append(recommendations)

# Output: List of top movie recommendations for each user in the train matrix
top_recommendations

# print size of top_recommendations
len(top_recommendations)


[['Baby Neptune: Discovering Water',
  'The Duel at Silver Creek',
  'Vegas in Space',
  'Plymptoons',
  'Spitfire Grill'],
 ["You're Invited to Mary-Kate and Ashley's Vacation Parties",
  'Fame',
  'Police Academy 3: Back in Training',
  'The Librarian: Quest for the Spear',
  'Spitfire Grill'],
 ['The Life and Times of Hank Greenberg',
  'Manhood',
  'Silent Service',
  'The Story of O',
  'Uncle Saddam'],
 ['The Life and Times of Hank Greenberg',
  'Manhood',
  'Silent Service',
  'The Story of O',
  'Uncle Saddam'],
 ["You're Invited to Mary-Kate and Ashley's Vacation Parties",
  'Manhood',
  'Frida',
  'Ozzy Osbourne: Crown Prince of Darkness',
  'Bride and Prejudice'],
 ["Overhaulin': Season 1",
  'Manhood',
  'Silent Service',
  'Horse Crazy',
  'Uncle Saddam'],
 ['The Life and Times of Hank Greenberg',
  'Manhood',
  'Silent Service',
  'The Story of O',
  'Uncle Saddam'],
 ['Oswald: Welcome to the Big City!',
  'The Pirate Movie',
  'The Strongest Man in the World',
  'The Fin

21923

In [44]:
print("Last version")

Last version


### Step 5: Model Evaluation
- We evaluate the performance of your ItemKNN algorithm using appropriate evaluation metrics such as Root Mean Squared Error (RMSE), Mean Absolute Error (MAE), or others.
- Split your dataset into training and testing sets to assess the model's predictive accuracy on unseen data.

In [45]:
train.shape

predicted_ratings_train.shape

(21923, 78)

(21923, 78)

In [46]:
import numpy as np
from sklearn.metrics import mean_absolute_error, mean_squared_error

def evaluate_model(train_matrix, predicted_ratings):
    """
    Evaluate the model's performance on the training data.

    Parameters:
        train_matrix (numpy.ndarray): Item-user matrix from the training data.
        predicted_ratings (pandas.DataFrame or numpy.ndarray): Predicted ratings DataFrame or array for the training data.

    Returns:
        float: Mean Absolute Error (MAE) on the training data.
        float: Root Mean Squared Error (RMSE) on the training data.
    """
    # Convert predicted_ratings to a numpy array if it's a DataFrame
    if isinstance(predicted_ratings, pd.DataFrame):
        predicted_ratings = predicted_ratings.to_numpy()

    # Ensure train_matrix and predicted_ratings have the same shape
    assert train_matrix.shape == predicted_ratings.shape, "Shapes of train_matrix and predicted_ratings are not consistent."

    # Initialize lists to store true and predicted ratings
    true_ratings = []
    pred_ratings = []

    # Iterate over each user and their ratings
    for user_id, user_ratings in enumerate(train_matrix):
        for movie_id, rating in enumerate(user_ratings):
            # Skip unrated movies
            if rating == 0:
                continue

            # Check if the indices are within the bounds of the predicted ratings array
            if user_id < predicted_ratings.shape[0] and movie_id < predicted_ratings.shape[1]:
                # Get the predicted rating for the corresponding movie
                pred_rating = predicted_ratings[user_id, movie_id]

                # Append the true and predicted ratings
                true_ratings.append(rating)
                pred_ratings.append(pred_rating)

    # Convert lists to numpy arrays
    true_ratings = np.array(true_ratings)
    pred_ratings = np.array(pred_ratings)

    # Calculate evaluation metrics
    mae = mean_absolute_error(true_ratings, pred_ratings)
    rmse = np.sqrt(mean_squared_error(true_ratings, pred_ratings))

    return mae, rmse

# Assuming train is the numpy array representing the item-user matrix
# Assuming predicted_ratings_train is the DataFrame or numpy array representing the predicted ratings for the training data

# Evaluate the model
mae, rmse = evaluate_model(train, predicted_ratings_train)

print("Mean Absolute Error (MAE) on Training Data:", mae)
print("Root Mean Squared Error (RMSE) on Training Data:", rmse)


Mean Absolute Error (MAE) on Training Data: 0.8620413962803354
Root Mean Squared Error (RMSE) on Training Data: 1.0296547112097671


### Step 6: Parameter Tuning
- Experiment with different parameters such as similarity threshold, neighborhood size, and similarity metric to optimize the performance of your ItemKNN algorithm.
- Use cross-validation or other techniques to tune these parameters and avoid overfitting.

1. **Import Necessary Libraries:**
   - We import the required libraries for performing grid search cross-validation (`GridSearchCV`), creating custom scorers (`make_scorer`), and utilizing the `NearestNeighbors` algorithm.

2. **Define Cosine Similarity Function:**
   - We define a custom function `cosine_similarity` to compute the cosine similarity between two vectors. This function calculates the dot product of the vectors and divides it by the product of their norms.

3. **Define Custom Scorer:**
   - We create a custom scorer `cosine_similarity_scorer` using `make_scorer`, which enables us to use cosine similarity as the scoring metric during grid search cross-validation.

4. **Define Parameter Grid:**
   - We specify a parameter grid `param_grid` containing the hyperparameters to be tuned. In this case, we're tuning the number of neighbors (`n_neighbors`) and the distance metric (`metric`) for the `NearestNeighbors` algorithm.

5. **Initialize NearestNeighbors Model:**
   - We initialize the `NearestNeighbors` model without specifying any hyperparameters.

6. **Create GridSearchCV Object:**
   - We create a `GridSearchCV` object named `grid_search` with the specified parameter grid, cross-validation strategy (5-fold cross-validation), and custom scoring metric (`cosine_similarity_scorer`).

7. **Fit the Data:**
   - We fit the `item_user_matrix` data to the `grid_search` object to perform hyperparameter tuning. `item_user_matrix` typically contains the item-item similarity matrix computed using collaborative filtering techniques.

8. **Get Best Hyperparameters:**
   - After fitting the data, we retrieve the best hyperparameters selected by the grid search using the `best_params_` attribute of the `grid_search` object.

9. **Print Best Parameters:**
   - Finally, we print the best hyperparameters obtained from the grid search.



`scikit-learn (sklearn)`:

- Scikit-learn is a popular machine learning library in Python that provides simple and efficient tools for data analysis and modeling.
- It includes various modules for tasks such as classification, regression, clustering, dimensionality reduction, and model selection.
- The GridSearchCV class from scikit-learn is used for hyperparameter tuning through grid search along with cross-validation.
- The make_scorer function allows you to create a custom scoring function for use with GridSearchCV.
- The NearestNeighbors class provides functionality for unsupervised nearest neighbors learning, which can be used for tasks such as finding k-nearest neighbors for a given data point.

In [47]:
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import NearestNeighbors
from sklearn.metrics import make_scorer
import numpy as np

# Define a custom scorer based on cosine similarity defined above
cosine_similarity_scorer = make_scorer(cosine_similarity)

# Define the parameter grid
param_grid = {
    'n_neighbors': [5, 10, 15, 30, 40],
    'metric': ['cosine', 'euclidean']
}

# Initialize NearestNeighbors model
knn_model = NearestNeighbors()

# Create the GridSearchCV object
grid_search = GridSearchCV(knn_model, param_grid, cv=5, scoring=cosine_similarity_scorer)

# Fit the data to perform hyperparameter tuning
grid_search.fit(train_matrix)  # train_matrix contains item-user matrix for the train set

# Get the best hyperparameters
best_params = grid_search.best_params_

print("Best parameters:", best_params)


c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py:993: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py", line 980, in _score
    scores = scorer(estimator, X_test, **score_params)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
TypeError: _BaseScorer.__call__() missing 1 required positional argument: 'y_true'

  warnings.warn(
c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py:993: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py", line 980, in _score
    scores = scorer(estimator, X_test, **score_

GridSearchCV(cv=5, estimator=NearestNeighbors(),
             param_grid={'metric': ['cosine', 'euclidean'],
                         'n_neighbors': [5, 10, 15, 30, 40]},
             scoring=make_scorer(cosine_similarity, response_method='predict'))

Best parameters: {'metric': 'cosine', 'n_neighbors': 5}


This code sets up a GridSearchCV object to perform hyperparameter tuning using the train set (train_matrix). It explores different combinations of hyperparameters specified in the param_grid, evaluates them using 5-fold cross-validation (cv=5), and uses the cosine_similarity scorer to optimize the model's performance based on cosine similarity. Finally, it prints the best hyperparameters found during the search.

We have to perform the calculation of the predicted ratings for the train-val set to generate predicted ratings in order to evaluate the performance of our trained model on a validation dataset. 

If we computed the similarity matrix again specifically for the train_val set, it would essentially mean that we are using a different set of similarity measures for predicting ratings compared to what we used during training. This approach could lead to inconsistencies and potentially degrade the performance of our model. Here's what could happen:

1. **Inconsistency**: The similarity measures computed for the train_val set might differ from those computed for the training set due to variations in the data. As a result, the predicted ratings based on these new similarity measures may not align well with the predictions made during training, leading to inconsistency in the model's behavior.

2. **Overfitting**: Computing a new similarity matrix specifically for the train_val set might lead to overfitting on the validation data. The model may capture noise or idiosyncrasies present in the train_val set, which may not generalize well to unseen data.

3. **Increased Complexity**: Computing the similarity matrix again for the train_val set adds computational complexity and redundancy, especially if the similarity computation process is resource-intensive. This can result in longer training times and increased resource utilization.

Overall, it's generally recommended to use the same similarity measures or neighborhood definitions for both training and validation sets to ensure consistency and generalizability of the model.

In [48]:
# Assuming you have already trained your model and obtained the item_neighborhoods_train dictionary

# Initialize an empty DataFrame to store predicted ratings for train_val
predicted_ratings_val = pd.DataFrame(index=val_matrix.index, columns=val_matrix.columns)

# Iterate over each user and their ratings in the train_val set
for user_id, user_ratings in val_matrix.iterrows():
    for movie_id, rating in user_ratings.items():
        # Skip if the rating is non-zero (indicating a rating given by the user)
        if rating != 0:
            continue
        
        # Check if the movie has a neighborhood defined
        if movie_id in item_neighborhoods_train:
            neighborhood = item_neighborhoods_train[movie_id]
            
            # Filter out movies from the neighborhood that the user has rated in the train set
            filtered_neighborhood = [neighbor_movie_id for neighbor_movie_id in neighborhood if neighbor_movie_id in user_ratings.index and user_ratings.loc[neighbor_movie_id] != 0]
            
            # Check if there are valid indices in the filtered neighborhood
            if len(filtered_neighborhood) > 0:
                # Calculate the predicted rating for the target movie based on the neighborhood
                neighbor_ratings = [user_ratings.loc[neighbor_movie_id] for neighbor_movie_id in filtered_neighborhood]
                
                # Calculate the mean rating using only the movies in the neighborhood that have been rated by the user
                predicted_rating = np.mean(neighbor_ratings)
            else:
                # If the filtered neighborhood is empty, assign the mean rating of all movies rated by the user
                predicted_rating = user_ratings[user_ratings != 0].mean()
            
            # Assign the predicted rating to the corresponding cell in the DataFrame
            predicted_ratings_val.at[user_id, movie_id] = predicted_rating

# Fill NaN values with mean ratings across all users
predicted_ratings_val.fillna(predicted_ratings_val.mean().mean(), inplace=True)


C:\Users\Jaume\AppData\Local\Temp\ipykernel_6308\2864728636.py:35: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  predicted_ratings_val.fillna(predicted_ratings_val.mean().mean(), inplace=True)


In [49]:
predicted_ratings_val.head()

predicted_ratings_val.shape

43       44    58    155      166   168   213   226   236   239   \
564620    3.5  3.50000   3.5   3.5  3.50000   3.5   3.5   3.5   3.5   3.5   
1430074   3.0  3.00000   3.0   3.0  3.00000   3.0   3.0   3.0   3.0   3.0   
2232480   2.0  2.00000   2.0   2.0  2.00000   2.0   2.0   2.0   2.0   2.0   
753886    5.0  3.52953   5.0   5.0  5.00000   5.0   5.0   5.0   5.0   5.0   
1504146   3.0  3.00000   3.0   3.0  3.52953   3.0   3.0   3.0   3.0   3.0   

         ...  1768  1793  1821  1829  1830  1839  1851  1854  1855  1903  
564620   ...   3.5   3.5   3.5   3.5   3.5   3.5   3.5   3.5   3.5   3.5  
1430074  ...   3.0   3.0   3.0   3.0   3.0   3.0   3.0   3.0   3.0   3.0  
2232480  ...   2.0   2.0   2.0   2.0   2.0   2.0   2.0   2.0   2.0   2.0  
753886   ...   5.0   5.0   5.0   5.0   5.0   5.0   5.0   5.0   5.0   5.0  
1504146  ...   3.0   3.0   3.0   3.0   3.0   3.0   3.0   3.0   3.0   3.0  

[5 rows x 78 columns]

(5481, 78)

Now we evaluate the model with the Validation item-user matrix.

In [50]:
# Now, you can evaluate the model using the evaluate_model function
mae, rmse = evaluate_model(val_matrix.to_numpy(), predicted_ratings_val)

print("Mean Absolute Error (MAE) on Validation Data:", mae)
print("Root Mean Squared Error (RMSE) on Validation Data:", rmse)


Mean Absolute Error (MAE) on Validation Data: 0.8629111739590473
Root Mean Squared Error (RMSE) on Validation Data: 1.0295637022864497


### Retraining of the model with the Train-Val set

In [51]:
# After the model evaluation on the validation set, we recalculate the similarity matrix
# of the model on the train-val data
item_similarity_matrix_train_val = calculate_item_similarity_matrix(train_val)

# We calculate the item neighborhoods for the train_val data 
item_neighborhoods_train_val = neighborhood_selection(item_user_array, index_to_movie_id, item_similarity_matrix_train_val)

### Step 7: Deployment

Once we have come up with the best parameters possible and trained the model with the whole train_validation set, we will test it on the test set.

In [52]:
test_matrix

43    44    58    155   166   168   213   226   236   239   ...  \
1276913   0.0   0.0   5.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
2076827   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
1628202   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
1110223   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
2229134   0.0   0.0   3.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
...       ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
1460578   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
164861    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
761741    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
491294    0.0   4.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
1974527   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   

         1768  1793  1821  1829  1830  1839  1851  1854  1855  1903  
1276913   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
2076827   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
1628202   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
1110223   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
2229134   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
...       ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
1460578   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
164861    0.0   0.0   0.0   0.0   0.0   0.0   0.0   3.0   0.0   0.0  
761741    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
491294    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
1974527   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  

[6852 rows x 78 columns]

In [53]:
# Check if there are NaN values in the test matrix
test_matrix.isnull().sum().sum()

0

In [54]:
# Now, we can evaluate the model's predicted ratings on the test set

# Initialize an empty DataFrame to store predicted ratings
predicted_ratings_test = pd.DataFrame(index=test_matrix.index, columns=test_matrix.columns)

# Iterate over each user-item pair in the training set
for user_id, user_ratings in test_matrix.iterrows():
    for movie_id, rating in user_ratings.items():
        
        # Skip if the rating is non-zero (indicating a rating given by the user)
        if rating != 0:
            continue
        
        # Check if the movie has a neighborhood defined
        if movie_id in item_neighborhoods_train_val:
            neighborhood = item_neighborhoods_train_val[movie_id]
            
            # Filter out movies from the neighborhood that the user has rated in the training set
            filtered_neighborhood = [neighbor_movie_id for neighbor_movie_id in neighborhood if neighbor_movie_id in user_ratings.index and user_ratings.loc[neighbor_movie_id] != 0]
            
            # Check if there are valid indices in the filtered neighborhood
            if len(filtered_neighborhood) > 0:
                # Calculate the predicted rating for the target movie based on the neighborhood
                neighbor_ratings = [user_ratings.loc[neighbor_movie_id] for neighbor_movie_id in filtered_neighborhood]
                
                # Calculate the mean rating using only the movies in the neighborhood that have been rated by the user
                predicted_rating = np.mean(neighbor_ratings)
            else:
                # If the filtered neighborhood is empty, assign the mean rating of all movies rated by the user
                predicted_rating = user_ratings[user_ratings != 0].mean()
            
            # Assign the predicted rating to the corresponding cell in the DataFrame
            predicted_ratings_test.at[user_id, movie_id] = predicted_rating

# Fill NaN values with mean ratings across all users
predicted_ratings_test.fillna(predicted_ratings_test.mean().mean(), inplace=True)

# Now, you can evaluate the model's predicted ratings on the test set
mae, rmse = evaluate_model(test_matrix.to_numpy(), predicted_ratings_test.to_numpy())

print("Mean Absolute Error (MAE) on Test Data using Predicted Ratings from Test Set:", mae)
print("Root Mean Squared Error (RMSE) on Test Data using Predicted Ratings from Test Set:", rmse)


Mean Absolute Error (MAE) on Test Data using Predicted Ratings from Test Set: 0.8606621073281191
Root Mean Squared Error (RMSE) on Test Data using Predicted Ratings from Test Set: 1.0307602501482604


C:\Users\Jaume\AppData\Local\Temp\ipykernel_6308\912451769.py:36: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  predicted_ratings_test.fillna(predicted_ratings_test.mean().mean(), inplace=True)


In [55]:
top_recommendations_test = []

# Iterate over each row (user) in the test_matrix
for user_id in test_matrix.index:
    # Get the actual user ID corresponding to the user index
    recommendations = get_top_recommendations(user_id, predicted_ratings_test, df)
    top_recommendations_test.append(recommendations)

# Output: List of top movie recommendations for each user in the test matrix
top_recommendations_test

# print size of top_recommendations
print("Size of top_recommendations_test:", len(top_recommendations_test))



[['Disorganized Crime',
  'First Knight',
  "You're Invited to Mary-Kate and Ashley's Vacation Parties",
  'Ozzy Osbourne: Crown Prince of Darkness',
  'The Librarian: Quest for the Spear'],
 ['The Life and Times of Hank Greenberg',
  'Manhood',
  'Silent Service',
  'The Story of O',
  'Uncle Saddam'],
 ['Hellraiser: Hellworld',
  'Sextette',
  'Latham Entertainment Presents: An All New Comedy Experience',
  'Bride and Prejudice',
  "Play'd: A Hip-Hop Story"],
 ['Black Adder',
  'Bride and Prejudice',
  'Persuasion',
  'Mrs. Soffel',
  'Mumford'],
 ["Overhaulin': Season 1",
  'Manhood',
  'Silent Service',
  'Horse Crazy',
  'Uncle Saddam'],
 ["Overhaulin': Season 1",
  'Manhood',
  'Silent Service',
  'Horse Crazy',
  'Uncle Saddam'],
 ["Overhaulin': Season 1",
  'Manhood',
  'Silent Service',
  'Horse Crazy',
  'Uncle Saddam'],
 ["Overhaulin': Season 1",
  'Manhood',
  'Silent Service',
  'Horse Crazy',
  'Uncle Saddam'],
 ["Overhaulin': Season 1",
  'Manhood',
  'Silent Service',
 

Size of top_recommendations_test: 6852


# Item-based Classification (ItemKNN)

### Step 1: Data preparation
- Ensure you have a dataset with user-item interactions. Each interaction should include the user ID, item ID, and the corresponding label or class for classification.
- Preprocess the data as needed, including handling missing values, encoding categorical variables, and splitting into training and testing sets.

For this step we are going to resuse the `item_user_matrix` that we created in the first model built. 

### Step 2: Compute Item Similarity


In [56]:
item_similarity_matrix_train.shape

(78, 78)

In [57]:
import numpy as np

def item_neighborhood_selection(similarity_matrix, k=None, threshold=None, item_ids=None):
    """
    Select a subset of similar items for each item based on similarity matrix.

    Parameters:
        similarity_matrix (numpy.ndarray): Item-item similarity matrix.
        k (int): Number of similar items to select (optional).
        threshold (float): Similarity threshold for selecting similar items (optional).
        item_ids (list): List of item IDs corresponding to rows/columns of the similarity matrix.

    Returns:
        dict: Dictionary containing similar items for each item.
    """
    num_items = similarity_matrix.shape[0]
    item_neighborhood = {}

    for i in range(num_items):
        if k is not None:
            # Select top-k similar items (excluding the item itself)
            similar_items_indices = np.argsort(similarity_matrix[i])[::-1][:k]
        elif threshold is not None:
            # Select items with similarity above threshold (excluding the item itself)
            similar_items_indices = np.where(similarity_matrix[i] > threshold)[0]

        # Remove the item itself from the neighborhood
        similar_items_indices = similar_items_indices[similar_items_indices != i]

        # Get the item ID corresponding to the current index
        current_item_id = item_ids[i] if item_ids is not None else i

        # Get the item IDs for the neighborhood
        neighborhood_item_ids = [item_ids[index] for index in similar_items_indices]

        # Store the similar items with the item's ID as the key
        item_neighborhood[current_item_id] = neighborhood_item_ids

    return item_neighborhood

# Example usage:
# Assuming you have an item-item similarity matrix 'item_similarity_matrix_train'
# and you want to select top-5 similar items for each item
k = 5
item_neighborhoods_classification_train = item_neighborhood_selection(item_similarity_matrix_train, k=k, item_ids=index_to_movie_id)

# Check if there are any items with empty neighborhoods
empty_neighborhoods = []

for item_id, neighborhood in item_neighborhoods_classification_train.items():
    if not neighborhood:
        empty_neighborhoods.append(item_id)

if empty_neighborhoods:
    print("Items with empty neighborhoods:", empty_neighborhoods)
else:
    print("No items with empty neighborhoods found.")


No items with empty neighborhoods found.


In [58]:
len(item_neighborhoods_classification_train)

78

### Step 3: Ratings classification selection

In [59]:
import numpy as np
import pandas as pd

def recommend_movies(train_matrix, item_neighborhoods, movie_id_to_index, num_movies=5):
    """
    Recommend top movies for each user based on item neighborhood.

    Parameters:
        train_matrix (np.ndarray or pd.DataFrame): Matrix containing user-item ratings in the train set.
        item_neighborhoods (dict): Dictionary containing similar items for each item.
        movie_id_to_index (dict): Dictionary mapping movie IDs to their corresponding indices in the train_matrix.
        num_movies (int): Number of movies to recommend for each user.

    Returns:
        pd.DataFrame: DataFrame containing predicted ratings for recommended movies for each user.
    """
    # Convert train_matrix to DataFrame if it's a numpy array
    if isinstance(train_matrix, np.ndarray):
        train_matrix = pd.DataFrame(train_matrix, index=np.arange(train_matrix.shape[0]), columns=np.arange(train_matrix.shape[1]))

    # Initialize an empty DataFrame to store predicted ratings
    predicted_ratings = pd.DataFrame(index=train_matrix.index, columns=train_matrix.columns)

    # Iterate over each user-item pair in the training set
    for user_id, user_ratings in train_matrix.iterrows():
        for movie_id, rating in user_ratings.items():
            
            # Skip if the rating is non-zero (indicating a rating given by the user)
            if rating != 0:
                continue
            
            # Check if the movie has a neighborhood defined
            if movie_id in item_neighborhoods:
                neighborhood = item_neighborhoods[movie_id]
                
                # Initialize a flag to track if the rating has been predicted
                rating_predicted = False
                
                # Iterate over the items in the neighborhood
                for neighbor_movie_id in neighborhood:
                    # Check if the neighbor movie has been rated by the user
                    if neighbor_movie_id in user_ratings.index and user_ratings.loc[neighbor_movie_id] != 0:
                        # Use the rating of the closest item in the neighborhood
                        predicted_rating = user_ratings.loc[neighbor_movie_id]
                        rating_predicted = True
                        break
                
                # If none of the items in the neighborhood have been rated, use the user's average rating
                if not rating_predicted:
                    if user_ratings[user_ratings != 0].empty:
                        # If the user hasn't rated any movies, use the global mean rating
                        predicted_rating = train_matrix[train_matrix != 0].mean().mean()
                    else:
                        # Use the average of the ratings given by the user
                        predicted_rating = user_ratings[user_ratings != 0].mean()
                
                # Assign the predicted rating to the corresponding cell in the DataFrame
                predicted_ratings.at[user_id, movie_id] = predicted_rating

    # Fill NaN values with mean ratings across all users
    predicted_ratings.fillna(predicted_ratings.mean().mean(), inplace=True)

    # Set the index of the DataFrame as the user ID of the train set
    predicted_ratings.index = train_matrix.index

    # Display the head of the predicted_ratings DataFrame
    print(predicted_ratings.head())

    return predicted_ratings

# Example usage:
# Assuming you have the train matrix, item neighborhood dictionary, and movie_id_to_index dictionary
# train_matrix, item_neighborhoods, movie_id_to_index = ...

# Recommend movies for each user in the train set
predicted_ratings_classification_train = recommend_movies(train_matrix, item_neighborhoods_classification_train, movie_id_to_index)

# Print the shape of the predicted ratings matrix
print("Shape of predicted ratings matrix:", predicted_ratings_classification_train.shape)


         43    44    58    155   166   168   213   226   236   239   ...  \
751126   2.50   2.5   2.0  2.50   2.0  2.50   2.5  2.50  2.50  2.50  ...   
1772875  3.75   5.0   5.0  3.75   5.0  3.75   3.0  3.75  3.75  3.75  ...   
1832869  4.00   4.0   4.0  4.00   4.0  4.00   4.0  4.00  4.00  4.00  ...   
342396   3.00   3.0   3.0  3.00   3.0  3.00   3.0  3.00  3.00  3.00  ...   
1506336  3.50   3.5   3.5  3.50   4.0  3.50   3.5  3.50  3.50  3.50  ...   

         1768  1793  1821  1829  1830      1839  1851      1854  1855  1903  
751126    2.5  2.50  2.50  2.50   2.0  2.500000  2.50  3.531045  2.50  2.50  
1772875   3.0  3.75  3.75  3.75   3.0  3.531045  3.75  4.000000  3.75  3.75  
1832869   4.0  4.00  4.00  4.00   4.0  4.000000  4.00  4.000000  4.00  4.00  
342396    3.0  3.00  3.00  3.00   3.0  3.000000  3.00  3.531045  3.00  3.00  
1506336   3.5  3.50  3.50  3.00   3.0  3.500000  3.50  4.000000  3.50  3.50  

[5 rows x 78 columns]
Shape of predicted ratings matrix: (21923, 78)


C:\Users\Jaume\AppData\Local\Temp\ipykernel_6308\1893350747.py:61: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  predicted_ratings.fillna(predicted_ratings.mean().mean(), inplace=True)


In [60]:
type(train_matrix)

pandas.core.frame.DataFrame

In [61]:
predicted_ratings_classification_train

43        44        58        155       166       168       213   \
751126   2.500000  2.500000  2.000000  2.500000  2.000000  2.500000  2.500000   
1772875  3.750000  5.000000  5.000000  3.750000  5.000000  3.750000  3.000000   
1832869  4.000000  4.000000  4.000000  4.000000  4.000000  4.000000  4.000000   
342396   3.000000  3.000000  3.000000  3.000000  3.000000  3.000000  3.000000   
1506336  3.500000  3.500000  3.500000  3.500000  4.000000  3.500000  3.500000   
...           ...       ...       ...       ...       ...       ...       ...   
1304853  3.333333  3.333333  3.531045  3.000000  3.333333  3.000000  3.333333   
185495   2.666667  2.666667  2.666667  2.666667  3.531045  2.666667  2.666667   
41317    2.666667  3.000000  3.000000  2.666667  3.000000  2.666667  2.666667   
796472   3.000000  3.000000  3.000000  3.000000  3.000000  3.000000  3.000000   
532583   2.000000  2.000000  2.000000  2.000000  2.000000  2.000000  2.000000   

             226       236       239   ...      1768      1793      1821  \
751126   2.500000  2.500000  2.500000  ...  2.500000  2.500000  2.500000   
1772875  3.750000  3.750000  3.750000  ...  3.000000  3.750000  3.750000   
1832869  4.000000  4.000000  4.000000  ...  4.000000  4.000000  4.000000   
342396   3.000000  3.000000  3.000000  ...  3.000000  3.000000  3.000000   
1506336  3.500000  3.500000  3.500000  ...  3.500000  3.500000  3.500000   
...           ...       ...       ...  ...       ...       ...       ...   
1304853  3.333333  3.333333  3.333333  ...  4.000000  3.333333  3.333333   
185495   2.666667  2.666667  2.666667  ...  2.666667  2.666667  2.666667   
41317    2.666667  2.666667  2.666667  ...  2.000000  2.666667  2.666667   
796472   3.000000  3.000000  3.000000  ...  3.000000  3.000000  3.000000   
532583   2.000000  2.000000  2.000000  ...  2.000000  2.000000  2.000000   

             1829      1830      1839      1851      1854      1855      1903  
751126   2.500000  2.000000  2.500000  2.500000  3.531045  2.500000  2.500000  
1772875  3.750000  3.000000  3.531045  3.750000  4.000000  3.750000  3.750000  
1832869  4.000000  4.000000  4.000000  4.000000  4.000000  4.000000  4.000000  
342396   3.000000  3.000000  3.000000  3.000000  3.531045  3.000000  3.000000  
1506336  3.000000  3.000000  3.500000  3.500000  4.000000  3.500000  3.500000  
...           ...       ...       ...       ...       ...       ...       ...  
1304853  3.333333  4.000000  3.333333  3.333333  3.333333  3.333333  3.333333  
185495   1.000000  2.666667  2.666667  2.666667  3.531045  2.666667  2.666667  
41317    2.666667  2.000000  2.666667  2.666667  3.000000  2.666667  2.666667  
796472   3.000000  3.000000  3.000000  3.000000  3.000000  3.000000  3.000000  
532583   2.000000  2.000000  2.000000  2.000000  2.000000  2.000000  2.000000  

[21923 rows x 78 columns]

### Step 4: Recommendations Generation

In [62]:
import pandas as pd

# Convert predicted_ratings_classification_train to a pandas DataFrame if it's a numpy array
if isinstance(predicted_ratings_classification_train, np.ndarray):
    # Use the length of train_matrix as the number of rows and items as columns
    num_users, num_items = train_matrix.shape
    predicted_ratings_classification_train = pd.DataFrame(predicted_ratings_classification_train, index=range(num_users), columns=range(num_items))

# Initialize a dictionary to store top recommendations for each user
top_recommendations_per_user = {}

# Iterate over each user in the train matrix
for user_id in train_matrix.index:
    # Get the top recommendations for the current user using predicted_ratings_classification_train
    recommendations = get_top_recommendations(user_id, predicted_ratings_classification_train, df)
    
    # Store the recommendations in the dictionary
    top_recommendations_per_user[user_id] = recommendations

# Print the top 5 recommendations for each user
for user_id, recommendations in top_recommendations_per_user.items():
    print(f"User {user_id} recommendations:", recommendations)


User 751126 recommendations: ['Disorganized Crime', 'The Life and Times of Hank Greenberg', 'Baby Neptune: Discovering Water', 'The Duel at Silver Creek', "Play'd: A Hip-Hop Story"]
User 1772875 recommendations: ['The Sandlot', "You're Invited to Mary-Kate and Ashley's Vacation Parties", 'Fame', 'Police Academy 3: Back in Training', 'Grumpy Old Men']
User 1832869 recommendations: ['The Life and Times of Hank Greenberg', 'Manhood', 'Silent Service', 'The Story of O', 'Uncle Saddam']
User 342396 recommendations: ['The Life and Times of Hank Greenberg', 'Manhood', 'Silent Service', 'The Story of O', 'Uncle Saddam']
User 1506336 recommendations: ['First Knight', 'Hostage', 'Fame', 'Crazy/Beautiful', 'Grumpy Old Men']
User 223269 recommendations: ["Overhaulin': Season 1", 'Manhood', 'Silent Service', 'Horse Crazy', 'Uncle Saddam']
User 1538616 recommendations: ['The Life and Times of Hank Greenberg', 'Manhood', 'Silent Service', 'The Story of O', 'Uncle Saddam']
User 1078346 recommendations

### Step 5: Model Evaluation (Item KNN Classification)

In [63]:
import numpy as np
import pandas as pd

# Assuming predicted_ratings_classification_train is your predicted ratings DataFrame or numpy array

# Ensure predicted_ratings_classification_train is a numpy array
if isinstance(predicted_ratings_classification_train, pd.DataFrame):
    predicted_ratings_classification_train = predicted_ratings_classification_train.to_numpy()

# Assuming train_matrix is the numpy array representing the item-user matrix

# Ensure train_matrix is a 2D array
if isinstance(train_matrix, pd.DataFrame):
    train_matrix = train_matrix.to_numpy()

if train_matrix.ndim == 1:
    train_matrix = np.expand_dims(train_matrix, axis=0)

# Evaluate the model
mae, rmse = evaluate_model(train, predicted_ratings_classification_train)

print("Mean Absolute Error (MAE) on Training Data:", mae)
print("Root Mean Squared Error (RMSE) on Training Data:", rmse)


Mean Absolute Error (MAE) on Training Data: 0.8620108905080502
Root Mean Squared Error (RMSE) on Training Data: 1.029664063289708


### Step 6: Parameter Tuning

Experiment with different parameters such as similarity threshold, neighborhood size, and similarity metric to optimize the performance of your ItemKNN algorithm.
Use techniques like cross-validation to tune these parameters and avoid overfitting.

In [64]:
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import NearestNeighbors
from sklearn.metrics import make_scorer
import numpy as np

# Define a custom scorer based on cosine similarity defined above
cosine_similarity_scorer = make_scorer(cosine_similarity)

# Define the parameter grid
param_grid = {
    'n_neighbors': [5, 10, 15, 30, 40],
    'metric': ['cosine', 'euclidean']
}

# Initialize NearestNeighbors model
knn_model = NearestNeighbors()

# Create the GridSearchCV object
grid_search = GridSearchCV(knn_model, param_grid, cv=5, scoring=cosine_similarity_scorer)

# Fit the data to perform hyperparameter tuning
grid_search.fit(val_matrix)  # val_matrix contains item-user matrix

# Get the best hyperparameters
best_params = grid_search.best_params_

print("Best parameters:", best_params)


c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py:993: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py", line 980, in _score
    scores = scorer(estimator, X_test, **score_params)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
TypeError: _BaseScorer.__call__() missing 1 required positional argument: 'y_true'

  warnings.warn(
c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py:993: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py", line 980, in _score
    scores = scorer(estimator, X_test, **score_

GridSearchCV(cv=5, estimator=NearestNeighbors(),
             param_grid={'metric': ['cosine', 'euclidean'],
                         'n_neighbors': [5, 10, 15, 30, 40]},
             scoring=make_scorer(cosine_similarity, response_method='predict'))

Best parameters: {'metric': 'cosine', 'n_neighbors': 5}


We are now going to obtain again the ratings for the full val set to evaluate the performance. 

In [65]:
# Assuming you have the best model after hyperparameter tuning
# best_model = ...

# Function to recalculate predictions for a given matrix using the trained model
def recalculate_predictions(matrix, item_neighborhoods):
    """
    Recalculate predictions for a given matrix using the trained model.

    Parameters:
        matrix (pd.DataFrame): Matrix containing user-item ratings.

    Returns:
        pd.DataFrame: DataFrame containing recalculated predicted ratings for each user.
    """
    # Initialize an empty DataFrame to store recalculated predicted ratings
    recalculated_predictions = pd.DataFrame(index=matrix.index, columns=matrix.columns)

    # Iterate over each user-item pair in the matrix
    for user_id, user_ratings in matrix.iterrows():
        for movie_id, rating in user_ratings.items():
            # Skip if the rating is non-zero (indicating a rating given by the user)
            if rating != 0:
                continue

            # Check if the movie has a neighborhood defined
            if movie_id in item_neighborhoods:
                neighborhood = item_neighborhoods[movie_id]

                # Initialize a flag to track if the rating has been predicted
                rating_predicted = False

                # Iterate over the items in the neighborhood
                for neighbor_movie_id in neighborhood:
                    # Check if the neighbor movie has been rated by the user
                    if neighbor_movie_id in user_ratings.index and user_ratings.loc[neighbor_movie_id] != 0:
                        # Use the rating of the closest item in the neighborhood
                        predicted_rating = user_ratings.loc[neighbor_movie_id]
                        rating_predicted = True
                        break

                # If none of the items in the neighborhood have been rated, use the user's average rating
                if not rating_predicted:
                    if user_ratings[user_ratings != 0].empty:
                        # If the user hasn't rated any movies, use the global mean rating
                        predicted_rating = matrix[matrix != 0].mean().mean()
                    else:
                        # Use the average of the ratings given by the user
                        predicted_rating = user_ratings[user_ratings != 0].mean()

                # Assign the predicted rating to the corresponding cell in the DataFrame
                recalculated_predictions.at[user_id, movie_id] = predicted_rating

    # Fill NaN values with mean ratings across all users
    recalculated_predictions.fillna(recalculated_predictions.mean().mean(), inplace=True)

    return recalculated_predictions


# Recalculate predictions for the validation set (train_val_matrix)
recalculated_val_predictions = recalculate_predictions(val_matrix, item_neighborhoods_classification_train)


C:\Users\Jaume\AppData\Local\Temp\ipykernel_6308\4246365781.py:54: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  recalculated_predictions.fillna(recalculated_predictions.mean().mean(), inplace=True)


In [66]:
recalculated_val_predictions

43        44    58    155       166   168   213   226   236   239   \
564620    3.5  3.500000   3.5   3.5  3.500000   3.5   3.5   3.5   3.5   3.5   
1430074   3.0  3.000000   3.0   3.0  3.000000   3.0   3.0   3.0   3.0   3.0   
2232480   2.0  2.000000   2.0   2.0  2.000000   2.0   2.0   2.0   2.0   2.0   
753886    5.0  3.529971   5.0   5.0  5.000000   5.0   5.0   5.0   5.0   5.0   
1504146   3.0  3.000000   3.0   3.0  3.529971   3.0   3.0   3.0   3.0   3.0   
...       ...       ...   ...   ...       ...   ...   ...   ...   ...   ...   
914457    1.0  1.000000   1.0   1.0  1.000000   1.0   1.0   1.0   1.0   1.0   
1227502   4.0  4.000000   4.0   4.0  4.000000   4.0   4.0   4.0   4.0   4.0   
2261255   2.0  2.000000   2.0   2.0  2.000000   2.0   2.0   2.0   2.0   2.0   
280795    4.0  4.000000   4.0   4.0  4.000000   4.0   4.0   4.0   4.0   4.0   
669635    2.0  2.000000   2.0   2.0  2.000000   2.0   2.0   2.0   2.0   2.0   

         ...  1768  1793  1821  1829  1830  1839  1851      1854  1855  1903  
564620   ...   3.5   3.5   3.5   3.5   3.5   3.5   3.5  3.500000   3.5   3.5  
1430074  ...   3.0   3.0   3.0   3.0   3.0   3.0   3.0  3.000000   3.0   3.0  
2232480  ...   2.0   2.0   2.0   2.0   2.0   2.0   2.0  2.000000   2.0   2.0  
753886   ...   5.0   5.0   5.0   5.0   5.0   5.0   5.0  5.000000   5.0   5.0  
1504146  ...   3.0   3.0   3.0   3.0   3.0   3.0   3.0  3.000000   3.0   3.0  
...      ...   ...   ...   ...   ...   ...   ...   ...       ...   ...   ...  
914457   ...   1.0   1.0   1.0   1.0   1.0   1.0   1.0  1.000000   1.0   1.0  
1227502  ...   4.0   4.0   4.0   4.0   4.0   4.0   4.0  4.000000   4.0   4.0  
2261255  ...   2.0   2.0   2.0   2.0   2.0   2.0   2.0  2.000000   2.0   2.0  
280795   ...   4.0   4.0   4.0   4.0   4.0   4.0   4.0  4.000000   4.0   4.0  
669635   ...   3.0   2.0   2.0   2.0   3.0   2.0   2.0  3.529971   2.0   2.0  

[5481 rows x 78 columns]

In [67]:
# Evaluate the model
mae, rmse = evaluate_model(val, recalculated_val_predictions)

print("Mean Absolute Error (MAE) on Train-Validation Data:", mae)
print("Root Mean Squared Error (RMSE) on Train-Validation Data:", rmse)

Mean Absolute Error (MAE) on Train-Validation Data: 0.8628879023045837
Root Mean Squared Error (RMSE) on Train-Validation Data: 1.0295661879159739


### Step 7: Deployment

Once we have all the metrics, we have to recalculate the ratings for the test set, we are going to repeat the same process for the test set.

In [68]:
# We have to reobtain the neighborhood for the train_val data
# We will use the already calculated item-item similarity matrix for train_val data
item_neighborhoods_classification_train_val = item_neighborhood_selection(item_similarity_matrix_train_val, k=5, item_ids=index_to_movie_id)

# Recalculate predictions for the validation set (test matrix)
recalculated_test_predictions = recalculate_predictions(test_matrix, item_neighborhoods_classification_train_val)

C:\Users\Jaume\AppData\Local\Temp\ipykernel_6308\4246365781.py:54: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  recalculated_predictions.fillna(recalculated_predictions.mean().mean(), inplace=True)


We also have to evaluate the metrics for the test set.

In [69]:
# Evaluate the model
mae, rmse = evaluate_model(test, recalculated_test_predictions)

print("Mean Absolute Error (MAE) on Test Data:", mae)
print("Root Mean Squared Error (RMSE) on Train-Validation Data:", rmse)

Mean Absolute Error (MAE) on Test Data: 0.8606565845456754
Root Mean Squared Error (RMSE) on Train-Validation Data: 1.0307653650000774
